In [ ]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

## Read in Measurements

In [ ]:
constant_sampling = pd.read_csv(r'1000OhmSampling.csv')

# Calculation Function for $\vartheta(R_{PT1000})$
$\vartheta(R_{PT1000}) = \frac{-\alpha R_0 + \sqrt{\alpha^2R_0^2 - 4\beta R_0 \left(R_0 - R_{PT1000}\right)}}{2\beta R_0}$

with
* $\alpha = 3.9083 \cdot 10^{-3}$
* $\beta = -5.7750 \cdot 10^{-7}$
* $R_0 = 1000~\Omega$

In [ ]:
R_zero = 1000.0
A = 3.9083E-3
B = -5.7750E-7

def calc_temp(resistance):
    temp = (-R_zero * A + np.sqrt(R_zero*R_zero * A * A - 4* R_zero * B * (R_zero - resistance)))/(2*R_zero*B)
    return temp

## Description of ADC Value

In [ ]:
print(constant_sampling['adc_results.pa2_raw'].describe())

--------------------
# Calculate Temperature from Resistance Value

In [ ]:
constant_sampling['temp_calculated'] = constant_sampling.apply(lambda row: calc_temp(row['ext_lf_corr']) , axis=1)


# Histograms -- Starting from Index 100

In [ ]:
fig, axes = plt.subplots(nrows=1, ncols=3, figsize=(28,6))
signal_list = [('adc_results.pa2_raw', 25), ('ext_lf_corr', 25), ('temp_calculated', 25)]
for ax,sig in zip(axes, signal_list):
    n, bins, patches = ax.hist(constant_sampling[sig[0]][100:], 25, density=1)
    mu = np.mean(constant_sampling[sig[0]][100:])
    sigma = np.std(constant_sampling[sig[0]][100:])
    y = ((1 / (np.sqrt(2 * np.pi) * sigma)) * np.exp(-0.5 * (1 / sigma * (bins - mu))**2))
    ax.plot(bins, y)
    ax.set_title('Histogram and Standard Deviation of '+sig[0])
plt.show()

# Startup of Moving Average Filter with $\alpha' = 0.005$

In [ ]:
fig, ax = plt.subplots(nrows=2, ncols=1, figsize=(28,6), sharex=True)
data = constant_sampling['ext_lf_corr'][:20]
ax[0].plot(constant_sampling['Time'][:20], data)
ax[1].plot(constant_sampling['Time'][:20], constant_sampling['temp_calculated'][:20])
plt.show()